In [0]:
# ======================================================================================
# ENVIRONMENT CONFIGURATION (AWS Academy Lab)
# Professional note: In production, we would use Databricks Secret Scopes
# to avoid exposing credentials, or CloudFormation / IaC so S3 data
# is automatically registered in the Databricks Data Catalog.
# ======================================================================================

from pyspark.sql.functions import current_timestamp, input_file_name

path_bronze_csv = "YOUR_PATH"

access_key = "YOUR_ACCESS_KEY"
secret_key = "YOUR_SECRET_KEY"
session_token = "YOUR_SESSION_TOKEN"

# 1. Read using the hidden _metadata column
# Unity Catalog requires explicitly selecting fields from the _metadata object
df_bronze = (
    spark.read
         .format("csv")
         .option("header", "true")
         .option("sep", ";")
         .option("inferSchema", "true")
         .option("fs.s3a.access.key", access_key)
         .option("fs.s3a.secret.key", secret_key)
         .option("fs.s3a.session.token", session_token)
         .option(
             "fs.s3a.aws.credentials.provider",
             "org.apache.hadoop.fs.s3a.TemporaryAWSCredentialsProvider"
         )
         .load(path_bronze_csv)
         # Select all CSV columns plus the source file path from metadata
         .select("*", "_metadata.file_path")
         .withColumnRenamed("file_path", "nm_arquivo_origem")
         .withColumn("dh_ingestao_bronze", current_timestamp())
)

# 2. Persist data into the Bronze layer
spark.sql("CREATE DATABASE IF NOT EXISTS cvm_p210")

# Tip: In the Bronze layer we use overwrite mode to ensure the S3 snapshot
# always reflects the current state, avoiding duplicated files that Spark
# may read multiple times due to wildcard (*) issues
df_bronze.write \
    .format("delta") \
    .mode("overwrite") \
    .option("overwriteSchema", "true") \
    .saveAsTable("cvm_p210.bronze_inf_diario")

print("Bronze table successfully created using Unity Catalog standards!")
display(spark.table("cvm_p210.bronze_inf_diario").limit(5))

print("Bronze layer updated with Unity Catalog metadata!")

Bronze criada com sucesso usando padrões do Unity Catalog!


TP_FUNDO_CLASSE CNPJ_FUNDO_CLASSE ID_SUBCLASSE DT_COMPTC VL_TOTAL VL_QUOTA VL_PATRIM_LIQ CAPTC_DIA RESG_DIA NR_COTST nm_arquivo_origem dh_ingestao_bronze CLASSES - FIF 00.017.024/0001-53 null 2026-01-02 1067199.26 41.630978 1198104.76 0.0 0.0 1 s3a://project-cvm-210-lab-471112952127/cvm-transactions-daily/ano=2026/mes=01/inf_diario_fi_202601.csv 2026-01-10T19:39:43.816Z CLASSES - FIF 00.017.024/0001-53 null 2026-01-05 1067797.26 41.649965 1198651.19 0.0 0.0 1 s3a://project-cvm-210-lab-471112952127/cvm-transactions-daily/ano=2026/mes=01/inf_diario_fi_202601.csv 2026-01-10T19:39:43.816Z CLASSES - FIF 00.017.024/0001-53 null 2026-01-06 1068412.18 41.6696883 1199218.81 0.0 0.0 1 s3a://project-cvm-210-lab-471112952127/cvm-transactions-daily/ano=2026/mes=01/inf_diario_fi_202601.csv 2026-01-10T19:39:43.816Z CLASSES - FIF 00.017.024/0001-53 null 2026-01-07 1069011.36 41.6884867 1199759.81 0.0 0.0 1 s3a://project-cvm-210-lab-471112952127/cvm-transactions-daily/ano=2026/mes=01/inf_diario_fi_202601.csv 2026-01-10T19:39:43.816Z CLASSES - FIF 00.017.024/0001-53 null 2026-01-08 1069607.59 41.705779 1200257.47 0.0 0.0 1 s3a://project-cvm-210-lab-471112952127/cvm-transactions-daily/ano=2026/mes=01/inf_diario_fi_202601.csv 2026-01-10T19:39:43.816Z

Bronze atualizada com metadados do Unity Catalog!


In [0]:
from pyspark.sql.functions import col, to_date, year, month, current_timestamp, coalesce
from delta.tables import DeltaTable

# 1. COLUMN HANDLING (CVM 175 vs Legacy Schema)
# Spark suggested the column 'CNPJ_FUNDO_CLASSE'.
# We use a dynamic approach to support both schemas without breaking the pipeline.
df_bronze = spark.table("cvm_p210.bronze_inf_diario")

# Detect which CNPJ column exists in the Bronze layer to avoid runtime errors
col_cnpj = "CNPJ_FUNDO_CLASSE" if "CNPJ_FUNDO_CLASSE" in df_bronze.columns else "CNPJ_FUNDO"

df_silver_novo = (
    df_bronze
        .select(
            col(col_cnpj).alias("CNPJ_FUNDO"),  # Standardize column name in the Silver layer
            "DT_COMPTC",
            "VL_QUOTA",
            "VL_PATRIM_LIQ",
            "CAPTC_DIA",
            "RESG_DIA",
            "nm_arquivo_origem"
        )
        .withColumn("DT_COMPTC", to_date(col("DT_COMPTC"), "yyyy-MM-dd"))
        .withColumn("VL_PATRIM_LIQ", col("VL_PATRIM_LIQ").cast("double"))
        .withColumn("CAPTC_DIA", col("CAPTC_DIA").cast("double"))
        .withColumn("RESG_DIA", col("RESG_DIA").cast("double"))
        .withColumn("ano", year(col("DT_COMPTC")))
        .withColumn("mes", month(col("DT_COMPTC")))
        .withColumn("dh_processamento_silver", current_timestamp())
        .filter("VL_PATRIM_LIQ > 0")
)

# 2. MERGE LOGIC (Duplicate Prevention)
if spark.catalog.tableExists("cvm_p210.silver_inf_diario"):
    print(">>> Silver table detected. Starting MERGE operation...")
    target_table = DeltaTable.forName(spark, "cvm_p210.silver_inf_diario")

    (
        target_table.alias("hist")
            .merge(
                df_silver_novo.alias("novos"),
                "hist.CNPJ_FUNDO = novos.CNPJ_FUNDO AND hist.DT_COMPTC = novos.DT_COMPTC"
            )
            .whenMatchedUpdateAll()
            .whenNotMatchedInsertAll()
            .execute()
    )
else:
    print(">>> Creating Silver table for the first time...")
    (
        df_silver_novo.write
            .format("delta")
            .mode("overwrite")
            .partitionBy("ano", "mes")
            .saveAsTable("cvm_p210.silver_inf_diario")
    )

# 3. PERFORMANCE OPTIMIZATION
spark.sql("OPTIMIZE cvm_p210.silver_inf_diario ZORDER BY (CNPJ_FUNDO)")

print("✅ Silver layer successfully completed!")
display(spark.table("cvm_p210.silver_inf_diario").limit(5))

>>> Criando Tabela Silver pela primeira vez...
✅ Camada Silver concluída com sucesso!


CNPJ_FUNDO DT_COMPTC VL_QUOTA VL_PATRIM_LIQ CAPTC_DIA RESG_DIA nm_arquivo_origem ano mes dh_processamento_silver 00.017.024/0001-53 2026-01-02 41.630978 1198104.76 0.0 0.0 s3a://project-cvm-210-lab-471112952127/cvm-transactions-daily/ano=2026/mes=01/inf_diario_fi_202601.csv 2026 1 2026-01-10T19:40:06.234Z 00.017.024/0001-53 2026-01-05 41.649965 1198651.19 0.0 0.0 s3a://project-cvm-210-lab-471112952127/cvm-transactions-daily/ano=2026/mes=01/inf_diario_fi_202601.csv 2026 1 2026-01-10T19:40:06.234Z 00.017.024/0001-53 2026-01-06 41.6696883 1199218.81 0.0 0.0 s3a://project-cvm-210-lab-471112952127/cvm-transactions-daily/ano=2026/mes=01/inf_diario_fi_202601.csv 2026 1 2026-01-10T19:40:06.234Z 00.017.024/0001-53 2026-01-07 41.6884867 1199759.81 0.0 0.0 s3a://project-cvm-210-lab-471112952127/cvm-transactions-daily/ano=2026/mes=01/inf_diario_fi_202601.csv 2026 1 2026-01-10T19:40:06.234Z 00.017.024/0001-53 2026-01-08 41.705779 1200257.47 0.0 0.0 s3a://project-cvm-210-lab-471112952127/cvm-transactions-daily/ano=2026/mes=01/inf_diario_fi_202601.csv 2026 1 2026-01-10T19:40:06.234Z

In [0]:
# ======================================================================================
# TECHNICAL NOTE & BUSINESS ASSUMPTIONS (DATA GOVERNANCE):
# 1. Due to banking secrecy regulations, the CVM does not provide granular
#    portability data from Payment Institutions (IPs) and Banks.
# 2. PORTABILITY PROXY:
#    Since there is no direct CPF-level mapping, portability is inferred by
#    monitoring anomalous inflows and outflows (Subscriptions and Redemptions).
# 3. BUSINESS RULE:
#    Net movements greater than 5% of the fund's Net Asset Value (NAV) within a
#    single month are classified as 'Portability Events', as they deviate from
#    organic behavior.
# ======================================================================================

from pyspark.sql.functions import col, sum, when, abs, round, avg, max, min

# 1. Aggregation and Strategic KPI Calculation
df_gold_final = (
    spark.table("cvm_p210.silver_inf_diario")
        .groupBy("CNPJ_FUNDO", "ano", "mes")
        .agg(
            sum("CAPTC_DIA").alias("total_subscriptions"),
            sum("RESG_DIA").alias("total_redemptions"),
            avg("VL_PATRIM_LIQ").alias("avg_net_asset_value"),
            max("VL_QUOTA").alias("max_nav_per_share"),
            min("VL_QUOTA").alias("min_nav_per_share")
        )
        .withColumn(
            "net_flow",
            round(col("total_subscriptions") - col("total_redemptions"), 2)
        )
)

# 2. Portability Classification and Fund Health Assessment
df_gold_insights = (
    df_gold_final
        .withColumn(
            "turnover_rate",
            round(
                (abs(col("total_subscriptions")) + abs(col("total_redemptions"))) /
                col("avg_net_asset_value"),
                4
            )
        )
        .withColumn(
            "is_portability_event",
            when(
                abs(col("net_flow")) > (col("avg_net_asset_value") * 0.05),
                "Yes"
            ).otherwise("No")
        )
        .withColumn(
            "business_classification",
            when(
                (col("is_portability_event") == "Yes") & (col("net_flow") > 0),
                "Inbound Portability (Growth Opportunity)"
            )
            .when(
                (col("is_portability_event") == "Yes") & (col("net_flow") < 0),
                "Outbound Portability (Capital Loss)"
            )
            .when(
                col("net_flow") > 0,
                "Organic Growth"
            )
            .otherwise(
                "Retail Redemption"
            )
        )
        # Monthly NAV Volatility (key driver analysis for portability behavior)
        .withColumn(
            "monthly_nav_variation_pct",
            round(
                ((col("max_nav_per_share") - col("min_nav_per_share")) /
                 col("min_nav_per_share")) * 100,
                2
            )
        )
)

# 3. Final Write to Gold Layer
(
    df_gold_insights.write
        .format("delta")
        .mode("overwrite")
        .saveAsTable("cvm_p210.gold_cvm210_analytics")
)

print("✨ Gold table successfully created with business insights and governance context.")
display(spark.table("cvm_p210.gold_cvm210_analytics"))


✨ Tabela Gold Finalizada com Insights de Negócio e Metadados.


CNPJ_FUNDO ano mes total_captacao total_resgate patrimonio_medio cota_maxima cota_minima fluxo_liquido taxa_rotatividade is_portabilidade classificacao_negocio variacao_cota_mes 05.575.327/0001-05 2026 1 0.0 0.0 5071568.078 127.434788912316 127.109504562542 0.0 0.0 Não Resgate de Varejo 0.26 06.288.668/0001-62 2026 1 0.0 3245286.23 1.186754030176E9 118.243365 115.745316 -3245286.23 0.0027 Não Resgate de Varejo 2.16 07.667.580/0001-14 2026 1 0.0 0.0 7.453653847E7 8.5289033843 8.3514559095 0.0 0.0 Não Resgate de Varejo 2.12 09.911.408/0001-90 2026 1 0.0 0.0 8.290341893200001E7 4.046541 4.015541 0.0 0.0 Não Resgate de Varejo 0.77 12.053.727/0001-16 2026 1 58178.87 135471.46000000002 2.4979700628E7 2.1208099 2.1091833 -77292.59 0.0078 Não Resgate de Varejo 0.55 13.409.667/0001-94 2026 1 0.0 0.0 2640590.122 7.15822638752 7.101246837096 0.0 0.0 Não Resgate de Varejo 0.8 15.674.503/0001-10 2026 1 0.0 28800.65 8411035.672 318.356418 317.240474 -28800.65 0.0034 Não Resgate de Varejo 0.35 17.898.668/0001-09 2026 1 0.0 0.0 1.71269235938E8 3.46645967 3.46090006 0.0 0.0 Não Resgate de Varejo 0.16 19.689.941/0001-02 2026 1 1000.0 1035.94 2.8254975075999998E7 2.474407438 2.406475425 -35.94 1.0E-4 Não Resgate de Varejo 2.82 20.649.608/0001-59 2026 1 0.0 0.0 1.6784672802E7 0.67303208 0.67080806 0.0 0.0 Não Resgate de Varejo 0.33 28.078.625/0001-95 2026 1 0.0 0.0 1.17083903124E8 2.2992556 2.2656416 0.0 0.0 Não Resgate de Varejo 1.48 29.722.392/0001-84 2026 1 0.0 0.0 1.66165824302E8 205.1818777 204.4843331 0.0 0.0 Não Resgate de Varejo 0.34 29.733.842/0001-34 2026 1 0.0 80791.69 2.07461689032E8 1.8469979 1.8359431 -80791.69 4.0E-4 Não Resgate de Varejo 0.6 35.618.006/0001-01 2026 1 0.0 0.0 1802536.7219999998 165.58006307 165.52341205 0.0 0.0 Não Resgate de Varejo 0.03 36.436.860/0001-10 2026 1 0.0 0.0 8.398600667E7 2.0967745 2.0453382 0.0 0.0 Não Resgate de Varejo 2.51 37.311.726/0001-55 2026 1 0.0 0.0 6.836409715E7 161.2283135 157.2607748 0.0 0.0 Não Resgate de Varejo 2.52 39.380.392/0001-05 2026 1 0.0 0.0 1.4004390036000002E7 1.326592 1.317617 0.0 0.0 Não Resgate de Varejo 0.68 40.498.341/0001-53 2026 1 0.0 0.0 8.1799123056E7 1.565993 1.561505 0.0 0.0 Não Resgate de Varejo 0.29 46.344.236/0001-46 2026 1 0.0 0.0 2.321954609E8 164.46035664 164.19329612 0.0 0.0 Não Resgate de Varejo 0.16 47.670.422/0001-38 2026 1 1065711.87 2722452.6 7.52261484452E8 1.3939905 1.389881 -1656740.73 0.005 Não Resgate de Varejo 0.3 47.794.998/0001-07 2026 1 0.0 10000.0 4117066.2619999996 1.5087784 1.4539598 -10000.0 0.0024 Não Resgate de Varejo 3.77 49.650.409/0001-42 2026 1 1.765694237E7 1.399857001E7 2.4735991242333332E8 1.39060334 1.38685243 3658372.36 0.128 Não Crescimento Orgânico 0.27 50.095.878/0001-26 2026 1 0.0 0.0 1.1069662179E8 1485.21099069 1485.21099069 0.0 0.0 Não Resgate de Varejo 0.0 51.726.488/0001-70 2026 1 0.0 0.0 1.8791330538E7 1.3427204 1.3399744 0.0 0.0 Não Resgate de Varejo 0.2 52.285.839/0001-17 2026 1 0.0 0.0 1265627.554 14.2560791 13.5924852 0.0 0.0 Não Resgate de Varejo 4.88 53.577.957/0001-61 2026 1 3.001358536E7 2220.0 3.05227394804E8 1.1972623 1.1944201 3.001136536E7 0.0983 Sim Portabilidade Receptora (Sucesso) 0.24 53.677.864/0001-09 2026 1 0.0 0.0 8457411.916 1.62741806 1.62406745 0.0 0.0 Não Resgate de Varejo 0.21 54.269.927/0001-50 2026 1 0.0 0.0 1122724.336 1.0381865 1.0362477 0.0 0.0 Não Resgate de Varejo 0.19 55.437.858/0001-00 2026 1 0.0 7000.0 7.528394793800001E7 1.1500346 1.1450052 -7000.0 1.0E-4 Não Resgate de Varejo 0.44 60.647.338/0001-61 2026 1 0.0 0.0 1.2903620589400001E8 1.07978921 1.06017456 0.0 0.0 Não Resgate de Varejo 1.85 62.546.455/0001-64 2026 1 0.0 0.0 7.908956004E7 1059.43297301 1055.85754065 0.0 0.0 Não Resgate de Varejo 0.34 63.892.223/0001-20 2026 1 0.0 0.0 7459455.084000001 1.003677 0.981574 0.0 0.0 Não Resgate de Varejo 2.25 04.589.378/0001-23 2026 1 0.0 3007.43 4942805.456 12.28930187 12.26746716 -3007.43 6.0E-4 Não Resgate de Varejo 0.18 05.222.547/0001-55 2026 1 0.0 227098.04 6.5892598736E7 7.7798332 7.76